In [1]:
import pandas as pd
import polars as pl

pd.set_option("display.max_rows", 25_000)
pd.set_option("display.max_columns", 500)
pl.Config.set_tbl_cols(500)
pl.Config.set_tbl_rows(10_000)

pd.options.display.float_format = "{:.4f}".format

bnf = pd.read_csv("BNF Rolling Pivots 3x Lev.csv")
nf = pd.read_csv("NF Rolling Pivots 4x Lev.csv")
midcp = pd.read_csv("MIDCP Rolling Pivots 4x Lev.csv")

In [2]:
bnf.head()

Unnamed: 0 Trade Type        Signal Generated At  \
0           0      SHORT  2018-01-01 15:15:00+05:30   
1           1       LONG  2018-01-04 11:15:00+05:30   
2           2      SHORT  2018-01-05 10:15:00+05:30   
3           3       LONG  2018-01-05 12:15:00+05:30   
4           4      SHORT  2018-01-08 10:15:00+05:30   

                  Entry Time  Entry Price  Initial SL  \
0  2018-01-02 09:15:00+05:30   25271.5500  25557.6500   
1  2018-01-04 12:15:00+05:30   25434.3000  25310.3000   
2  2018-01-05 11:15:00+05:30   25529.5000  25575.2500   
3  2018-01-05 13:15:00+05:30   25570.8000  25508.4000   
4  2018-01-08 11:15:00+05:30   25717.8500  25771.5000   

                   Exit Time  Exit Price         Remarks  Points Captured  \
0  2018-01-04 12:15:00+05:30  25434.3000        Reversed        -162.7500   
1  2018-01-05 11:15:00+05:30  25529.5000        Reversed          95.2000   
2  2018-01-05 13:15:00+05:30  25570.8000        Reversed         -41.3000   
3  2018-01-08 11:15:00+05:30  25717.8500        Reversed         147.0500   
4  2018-01-09 09:15:00+05:30  25771.5000  Initial SL Hit         -53.6500   

   Points w CS      Qty  Leverage         PnL    PnL w CS    ROI%  ROI% w CS  \
0    -167.8206 118.7106         3 -19320.1446 -19922.0766 -1.9320    -1.9922   
1      90.1036 117.9510         3  11228.9310  10627.8081  1.1229     1.0628   
2     -46.4100 117.5111         3  -4853.2090  -5453.6944 -0.4853    -0.5454   
3     141.9211 117.3213         3  17252.1001  16650.3748  1.7252     1.6650   
4     -58.7989 116.6505         3  -6258.2992  -6858.9250 -0.6258    -0.6859   

   Trade Year  
0        2018  
1        2018  
2        2018  
3        2018  
4        2018

In [3]:
bnf["Index"] = "BANKNIFTY"
nf["Index"] = "NIFTY"
midcp["Index"] = "MIDCPNIFTY"

In [4]:
combined_df = pd.concat([bnf, nf, midcp], ignore_index=True)
combined_df_sorted = combined_df.sort_values(by="Entry Time")
combined_df_sorted.loc[
    (combined_df_sorted["Trade Year"] >= 2017)
    & (combined_df_sorted["Trade Year"] < 2022),
    "ROI% w CS",
] /= 2
combined_df_sorted.loc[combined_df_sorted["Trade Year"] >= 2022, "ROI% w CS"] /= 3
combined_df_sorted["DD%"] = (
    combined_df_sorted["ROI% w CS"].cumsum()
    - combined_df_sorted["ROI% w CS"].cumsum().cummax()
)
combined_df_sorted.drop(columns=["Unnamed: 0"], inplace=True)
combined_df_sorted

Trade Type        Signal Generated At                 Entry Time  \
1789      SHORT  2018-01-01 11:15:00+05:30  2018-01-01 12:15:00+05:30   
0         SHORT  2018-01-01 15:15:00+05:30  2018-01-02 09:15:00+05:30   
1          LONG  2018-01-04 11:15:00+05:30  2018-01-04 12:15:00+05:30   
2         SHORT  2018-01-05 10:15:00+05:30  2018-01-05 11:15:00+05:30   
1790      SHORT  2018-01-05 10:15:00+05:30  2018-01-05 11:15:00+05:30   
3          LONG  2018-01-05 12:15:00+05:30  2018-01-05 13:15:00+05:30   
1791       LONG  2018-01-05 12:15:00+05:30  2018-01-05 13:15:00+05:30   
4         SHORT  2018-01-08 10:15:00+05:30  2018-01-08 11:15:00+05:30   
1792      SHORT  2018-01-08 12:15:00+05:30  2018-01-08 13:15:00+05:30   
1793      SHORT  2018-01-08 15:15:00+05:30  2018-01-09 09:15:00+05:30   
1794       LONG  2018-01-09 10:15:00+05:30  2018-01-09 11:15:00+05:30   
1795      SHORT  2018-01-09 10:15:00+05:30  2018-01-09 11:15:00+05:30   
1796       LONG  2018-01-09 10:15:00+05:30  2018-01-09 11:15:00+05:30   
6         SHORT  2018-01-09 10:15:00+05:30  2018-01-09 11:15:00+05:30   
7          LONG  2018-01-09 10:15:00+05:30  2018-01-09 11:15:00+05:30   
5          LONG  2018-01-09 10:15:00+05:30  2018-01-09 11:15:00+05:30   
1797      SHORT  2018-01-09 12:15:00+05:30  2018-01-09 13:15:00+05:30   
9         SHORT  2018-01-09 12:15:00+05:30  2018-01-09 13:15:00+05:30   
8          LONG  2018-01-09 12:15:00+05:30  2018-01-09 13:15:00+05:30   
10        SHORT  2018-01-09 14:15:00+05:30  2018-01-09 15:15:00+05:30   
1798      SHORT  2018-01-10 10:15:00+05:30  2018-01-10 11:15:00+05:30   
1799       LONG  2018-01-10 12:15:00+05:30  2018-01-10 13:15:00+05:30   
11         LONG  2018-01-10 12:15:00+05:30  2018-01-10 13:15:00+05:30   
13        SHORT  2018-01-11 13:15:00+05:30  2018-01-11 14:15:00+05:30   
12         LONG  2018-01-11 13:15:00+05:30  2018-01-11 14:15:00+05:30   
1800      SHORT  2018-01-11 13:15:00+05:30  2018-01-11 14:15:00+05:30   
1801      SHORT  2018-01-12 10:15:00+05:30  2018-01-12 11:15:00+05:30   
14        SHORT  2018-01-12 10:15:00+05:30  2018-01-12 11:15:00+05:30   
15         LONG  2018-01-12 13:15:00+05:30  2018-01-12 14:15:00+05:30   
1802       LONG  2018-01-12 13:15:00+05:30  2018-01-12 14:15:00+05:30   
16        SHORT  2018-01-15 15:15:00+05:30  2018-01-16 09:15:00+05:30   
17         LONG  2018-01-16 11:15:00+05:30  2018-01-16 12:15:00+05:30   
1803      SHORT  2018-01-16 13:15:00+05:30  2018-01-16 14:15:00+05:30   
1804      SHORT  2018-01-16 15:15:00+05:30  2018-01-17 09:15:00+05:30   
18         LONG  2018-01-17 12:15:00+05:30  2018-01-17 13:15:00+05:30   
19        SHORT  2018-01-18 10:15:00+05:30  2018-01-18 11:15:00+05:30   
1805       LONG  2018-01-18 10:15:00+05:30  2018-01-18 11:15:00+05:30   
1806      SHORT  2018-01-18 12:15:00+05:30  2018-01-18 13:15:00+05:30   
1807       LONG  2018-01-19 11:15:00+05:30  2018-01-19 12:15:00+05:30   
1808      SHORT  2018-01-19 13:15:00+05:30  2018-01-19 14:15:00+05:30   
20         LONG  2018-01-19 13:15:00+05:30  2018-01-19 14:15:00+05:30   
1809       LONG  2018-01-22 10:15:00+05:30  2018-01-22 11:15:00+05:30   
21        SHORT  2018-01-25 10:15:00+05:30  2018-01-25 11:15:00+05:30   
22        SHORT  2018-01-29 14:15:00+05:30  2018-01-29 15:15:00+05:30   
23         LONG  2018-01-30 15:15:00+05:30  2018-01-31 09:15:00+05:30   
1810      SHORT  2018-01-31 10:15:00+05:30  2018-01-31 11:15:00+05:30   
24        SHORT  2018-01-31 15:15:00+05:30  2018-02-01 09:15:00+05:30   
25         LONG  2018-02-01 10:15:00+05:30  2018-02-01 11:15:00+05:30   
1811      SHORT  2018-02-01 10:15:00+05:30  2018-02-01 11:15:00+05:30   
26        SHORT  2018-02-01 14:15:00+05:30  2018-02-01 15:15:00+05:30   
27         LONG  2018-02-02 11:15:00+05:30  2018-02-02 12:15:00+05:30   
1812       LONG  2018-02-02 11:15:00+05:30  2018-02-02 12:15:00+05:30   
1813      SHORT  2018-02-02 13:15:00+05:30  2018-02-02 14:15:00+05:30   
28        SHORT  2018-02-02 13:15:00+05:30  2018-02-02 14:15:00

In [47]:
stats_df8 = pd.DataFrame(
    index=range(2017, 2025),
    columns=[
        "Total ROI",
        "Total Trades",
        "Win Rate",
        "Avg Profit% per Trade",
        "Avg Loss% per Trade",
        "Max Drawdown",
        "ROI/DD Ratio",
    ],
)
combined_df_sorted = combined_df_sorted
# Iterate over each year
for year in range(2017, 2025):
    # Filter trades for the current year
    year_trades = combined_df_sorted[(combined_df_sorted["Trade Year"] == year)]

    # Calculate total ROI
    total_roi = year_trades["ROI% w CS"].sum()

    # Calculate total number of trades
    total_trades = len(year_trades)

    # Calculate win rate
    win_rate = (year_trades["ROI% w CS"] > 0).mean() * 100

    # Calculate average profit per trade
    avg_profit = year_trades[year_trades["ROI% w CS"] > 0]["ROI% w CS"].mean()

    # Calculate average loss per trade
    avg_loss = year_trades[year_trades["ROI% w CS"] < 0]["ROI% w CS"].mean()

    # Calculate maximum drawdown
    max_drawdown = (
        year_trades["ROI% w CS"].cumsum() - year_trades["ROI% w CS"].cumsum().cummax()
    ).min()

    # Calculate ROI/DD ratio
    roi_dd_ratio = total_roi / abs(max_drawdown)

    # Store the statistics in the DataFrame
    stats_df8.loc[year] = [
        total_roi,
        total_trades,
        win_rate,
        avg_profit,
        avg_loss,
        max_drawdown,
        roi_dd_ratio,
    ]

# Calculate overall statistics
overall_total_roi = stats_df8["Total ROI"].sum()
overall_total_trades = stats_df8["Total Trades"].sum()
overall_win_rate = (combined_df_sorted["ROI% w CS"] > 0).mean() * 100
overall_avg_profit = combined_df_sorted[combined_df_sorted["ROI% w CS"] > 0][
    "ROI% w CS"
].mean()
overall_avg_loss = combined_df_sorted[combined_df_sorted["ROI% w CS"] < 0][
    "ROI% w CS"
].mean()
overall_max_drawdown = (
    combined_df_sorted["ROI% w CS"].cumsum()
    - combined_df_sorted["ROI% w CS"].cumsum().cummax()
).min()
overall_roi_dd_ratio = overall_total_roi / abs(overall_max_drawdown)

# Store the overall statistics in the DataFrame
stats_df8.loc["Overall"] = [
    overall_total_roi,
    overall_total_trades,
    overall_win_rate,
    overall_avg_profit,
    overall_avg_loss,
    overall_max_drawdown,
    overall_roi_dd_ratio,
]
stats_df8

Total ROI Total Trades Win Rate Avg Profit% per Trade  \
2018      60.2264          568  46.1268                1.0320   
2019      87.9074          549  45.1730                1.1803   
2020     134.3168          504  38.8889                2.7759   
2021     134.9531          555  44.6847                1.5717   
2022      83.1843          804  41.9154                1.1300   
2023      63.0212          803  40.9714                0.7751   
2024      26.8428          380  39.7368                1.0046   
Overall  590.4519    4163.0000  42.5414                1.2899   

        Avg Loss% per Trade Max Drawdown ROI/DD Ratio  
2018                -0.6868     -14.5849       4.1294  
2019                -0.6805     -25.4072       3.4599  
2020                -1.3304     -37.2506       3.6058  
2021                -0.8300     -28.8289       4.6812  
2022                -0.6373     -22.3712       3.7184  
2023                -0.4050     -16.6655       3.7815  
2024                -0.5452     -18.0535       1.4868  
Overall             -0.7082     -52.4592      11.2554

In [49]:
combined_df_sorted.to_csv('Combined Rolling Pivots BNF NF MIDCP 3 4 4.csv')